In [37]:
# needed to load the REBEL model
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer, pipeline
import math
import torch

# wrapper for wikipedia API
import wikipedia

# scraping of web articles
from newspaper import Article
# google news scraping
from GoogleNews import GoogleNews

# graph visualization
from pyvis.network import Network

# show HTML in notebook
import IPython

from keybert import KeyBERT

from sentence_transformers import SentenceTransformer
import numpy as np
import nltk
import re
from typing import List, Tuple, Union

import spacy

import inspect
import os

import ollama
from tqdm import tqdm
import time

In [2]:
nltk.download('stopwords')
nlp = spacy.load("en_core_web_sm")


[nltk_data] Downloading package stopwords to
[nltk_data]     /home/niamatzawad/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [3]:
tokenizer = AutoTokenizer.from_pretrained("Babelscape/rebel-large")
model = AutoModelForSeq2SeqLM.from_pretrained("Babelscape/rebel-large")

In [12]:
def extract_relations_from_model_output(text): #From REBEL model code
    relations = []
    relation, subject, relation, object_ = '', '', '', ''
    text = text.strip()
    current = 'x'
    text_replaced = text.replace("<s>", "").replace("<pad>", "").replace("</s>", "")
    for token in text_replaced.split():
        if token == "<triplet>":
            current = 't'
            if relation != '':
                relations.append({
                    'head': subject.strip(),
                    'type': relation.strip(),
                    'tail': object_.strip()
                })
                relation = ''
            subject = ''
        elif token == "<subj>":
            current = 's'
            if relation != '':
                relations.append({
                    'head': subject.strip(),
                    'type': relation.strip(),
                    'tail': object_.strip()
                })
            object_ = ''
        elif token == "<obj>":
            current = 'o'
            relation = ''
        else:
            if current == 't':
                subject += ' ' + token
            elif current == 's':
                object_ += ' ' + token
            elif current == 'o':
                relation += ' ' + token
    if subject != '' and relation != '' and object_ != '':
        relations.append({
            'head': subject.strip(),
            'type': relation.strip(),
            'tail': object_.strip()
        })
    return relations

In [3]:
class KeywordExtractor():
    def __init__(self):
        self.pipe = pipeline("token-classification", model="eventdata-utd/conflibert-named-entity-recognition", tokenizer="eventdata-utd/conflibert-named-entity-recognition")
        self.kw_model = KeyBERT()
        self.stopwords = set(nltk.corpus.stopwords.words('english'))
        self.semantic_matcher = None
        
    def sanitize_and_repair(func):
        def wrapper(self, *args, **kwargs):
            phrases = func(self, *args, **kwargs)
            for i, phrase in enumerate(phrases):
                phrase = phrase.strip()
                phrase = phrase.lower()
                phrase = re.sub(r'[,\.!?]', ' ', phrase)
                phrase = re.sub(r'[^a-z0-9\s]', ' ', phrase)
                phrase = re.sub(r"^\s*(?:the|a)\s+", "", phrase, flags=re.IGNORECASE)
                phrase = re.sub(r'\s+', ' ', phrase)
                phrases[i] = phrase
            return phrases
        return wrapper

    def remove_stopwords(func):
        def wrapper(self, *args, **kwargs):
            phrases = func(self, *args, **kwargs)
            filtered_words = []
            for phrase in phrases:
                if phrase.lower() not in self.stopwords:
                    filtered_words.append(" ".join([token for token in phrase.split() if token.lower() not in self.stopwords]))
                   
            return filtered_words
        return wrapper

    @remove_stopwords 
    @sanitize_and_repair
    def extract_named_entities(self, doc):
        results = self.pipe(doc)
        named_entities = []
        for i, result in enumerate(results):
            if result["entity"] != "O" and result["entity"].split("-")[1] not in ["Quantity","Temporal","Money"]:
                if "B-" in result["entity"]:
                    j = i + 1
                    while j < len(results):
                        if "B-" in results[j]["entity"]:
                            break
                        j +=1
                    named_entities.append(" ".join(results[x]["word"] for x in range(i,j)))
        return named_entities
        
   

    @sanitize_and_repair
    @remove_stopwords
    def extract_keywords(self, doc):
        return [k[0] for k in self.kw_model.extract_keywords(doc)]
    
    
    

In [89]:
kwe = KeywordExtractor()
doc = """Several hundred residents of a drug-torn neighborhood marched through the
    streets Sunday in an protest over crack cocaine spurred by weekend shootings
    that left 2 people dead and 10 injured.
    
    ''We are going to march and shout and sing and pray till this crack cocaine is
    completely eradicated from our community,'' said the Rev. Cecil Williams, who
    led the march through the Ocean View neighborhood.
    
    Although the march and rally had been planned for several weeks, a drive-by
    ambush and another shooting less than two miles away in the Bayview-Hunters
    Point district gave people another reason to participate, Mr. Williams said."""
named_entities = (kwe.extract_named_entities(doc))

Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


In [94]:
doc = """Students at Columbia University Law School are protesting what they fear may be
the closing of a popular clinic that offers legal help to victims of AIDS
discrimination and practical experience for credit to the students who represent
them.

The students are also rallying to support the clinic's instructor, who does not
have tenure and who the students fear may not be rehired by the university.

At the heart of the dispute is a larger debate between advocates of such
practical studies in the education of a lawyer and traditionalists, who believe
the clinics detract from the school's academic image.

On Thursday, about 200 students occupied part of the law school's main building,
alternately chanting and studying.

No Decision on Clinic

''One-two-three-four, do not shut the clinic door!'' the students chanted,
clutching heavy textbooks with titles like ''Gratuitous Transfers.'' They also
sang a student-written song called ''A Kinder, Gentler Law School.''"""
named_entities = (kwe.extract_named_entities(doc))

In [4]:
s.get_most_similar_entity("Police")

In [95]:
named_entities

['students',
 'columbia university law school',
 'clinic',
 'victims',
 'students',
 'students',
 'clinic instructor',
 'students',
 'university',
 'advocates',
 'traditional ists',
 'school',
 '200',
 'students',
 'part',
 'law school main building',
 'clinic',
 'students',
 'student',
 'law']

In [91]:
s = SemanticSimilarity()
s.generate_reference(named_entities)
s.disambiguated_reference_list

['residents',
 'drug torn neighborhood',
 'streets',
 'people',
 'community',
 'rev cecil williams',
 'ocean view neighborhood',
 'bay view hunters point district']

In [93]:
s.generate_reference(named_entities)
s.disambiguated_reference_list

['residents',
 'drug torn neighborhood',
 'streets',
 'people',
 'community',
 'rev cecil williams',
 'ocean view neighborhood',
 'bay view hunters point district',
 'students',
 'columbia university law school',
 'clinic',
 'victims',
 'university',
 'advocates',
 'traditional ists',
 '200',
 'part',
 'law']

In [104]:
s.get_most_similar_relation("street")

In [5]:
class KB():
    def __init__(self):
        self.relations = []

    def are_relations_equal(self, r1, r2):
        return all(r1[attr] == r2[attr] for attr in ["head", "type", "tail"])

    def exists_relation(self, r1):
        return any(self.are_relations_equal(r1, r2) for r2 in self.relations)

    def add_relation(self, r):
        if not self.exists_relation(r):
            self.relations.append(r)

    def print(self):
        print("Relations:")
        for r in self.relations:
            print(f"  {r}")

NameError: name 'named_entities' is not defined

In [40]:
def rebel_get_relations(text):
    model_inputs = tokenizer(text, max_length=512, padding=True, truncation=True,
                            return_tensors='pt')
    # Generate
    gen_kwargs = {
        "max_length": 216,obj = re.sub("\/","_", obj)
        "length_penalty": 0,
        "num_beams": 3,
        "num_return_sequences": 3
    }

    
    generated_tokens = model.generate(
        **model_inputs,
        **gen_kwargs,
    )
    decoded_preds = tokenizer.batch_decode(generated_tokens, skip_special_tokens=False)

    for sentence_pred in decoded_preds:
        relations = extract_relations_from_model_output(sentence_pred)
        print(relations)


In [307]:
# build a knowledge base from text
def from_small_text_to_kb(text, verbose=False):
    kb = KB()

    # Tokenizer text
    model_inputs = tokenizer(text, max_length=512, padding=True, truncation=True,
                            return_tensors='pt')
    print(model_inputs)

    if verbose:
        print(f"Num tokens: {len(model_inputs['input_ids'][0])}")

    # Generate
    gen_kwargs = {
        "max_length": 216,
        "length_penalty": 0,
        "num_beams": 3,
        "num_return_sequences": 3
    }

    
    generated_tokens = model.generate(
        **model_inputs,
        **gen_kwargs,
    )
    decoded_preds = tokenizer.batch_decode(generated_tokens, skip_special_tokens=False)

    # create kb
    for sentence_pred in decoded_preds:
        relations = extract_relations_from_model_output(sentence_pred)
        for r in relations:
            kb.add_relation(r)

    return kb

In [50]:
# test the `from_small_text_to_kb` function

    text = """Several hundred residents of a drug-torn neighborhood marched through the
    streets Sunday in an protest over crack cocaine spurred by weekend shootings
    that left 2 people dead and 10 injured.
    
    ''We are going to march and shout and sing and pray till this crack cocaine is
    completely eradicated from our community,'' said the Rev. Cecil Williams, who
    led the march through the Ocean View neighborhood.
    
    Although the march and rally had been planned for several weeks, a drive-by
    ambush and another shooting less than two miles away in the Bayview-Hunters
    Point district gave people another reason to participate, Mr. Williams said."""

kb = from_small_text_to_kb(text, verbose=True)
kb.print()

{'input_ids': tensor([[    0, 29182,  6317,  1196,     9,    10,  1262,    12, 25566,  3757,
         15199,   149,     5, 50118, 24769,  2580,   395,    11,    41,  2790,
            81,  7009,  9890, 18272,    30,   983,  9272, 50118,  6025,   314,
           132,    82,  1462,     8,   158,  1710,     4, 50118, 50118, 17809,
           170,    32,   164,     7,  6674,     8, 18066,     8,  7884,     8,
         10745,  6612,    42,  7009,  9890,    16, 50118, 28655, 25193,  5554,
            31,    84,   435, 10559,    26,     5,  7161,     4, 28703,  1604,
             6,    54, 50118,  1329,     5,  6674,   149,     5,  5860,  3756,
          3757,     4, 50118, 50118, 13863,     5,  6674,     8,  2669,    56,
            57,  1904,    13,   484,   688,     6,    10,  1305,    12,  1409,
         50118,  3146,  3810,     8,   277,  1094,   540,    87,    80,  1788,
           409,    11,     5,  1501,  5877,    12, 38831,  2696, 50118, 20416,
          1418,   851,    82,   277,  

In [53]:
import ollama


template = f"""Task:Generate triplets from the following text.
    Instructions'
    The triplet should be in the format (<subject>, <relation type>, <object>)
    The subject and object should refer to specific entities.
    The relation type should refer to an action
    
    The text is:
    Several hundred residents of a drug-torn neighborhood marched through the
    streets Sunday in an protest over crack cocaine spurred by weekend shootings
    that left 2 people dead and 10 injured.
    
    ''We are going to march and shout and sing and pray till this crack cocaine is
    completely eradicated from our community,'' said the Rev. Cecil Williams, who
    led the march through the Ocean View neighborhood.
    
    Although the march and rally had been planned for several weeks, a drive-by
    ambush and another shooting less than two miles away in the Bayview-Hunters
    Point district gave people another reason to participate, Mr. Williams said"""


response = ollama.generate(model='mistral', prompt=template)
print(response)

{'model': 'mistral', 'created_at': '2024-04-18T19:30:56.99330289Z', 'response': ' 1. (Several hundred residents, marched, through the streets)\n2. (Residents of a drug-torn neighborhood, protested, crack cocaine)\n3. (Rev. Cecil Williams, led, march and shout and sing and pray)\n4. (People, participated, in the march and rally)\n5. (Weekend shootings, left, 2 people dead and 10 injured)\n6. (Drive-by ambush and another shooting, gave, people another reason to participate)\n7. (Rev. Cecil Williams, said, eradicated from our community)', 'done': True, 'context': [733, 16289, 28793, 28705, 10290, 28747, 23342, 22212, 1074, 477, 272, 2296, 2245, 28723, 13, 2287, 3133, 8373, 28742, 13, 2287, 415, 2629, 7081, 1023, 347, 297, 272, 5032, 325, 28789, 16566, 6550, 523, 21380, 1212, 6550, 523, 2814, 12970, 13, 2287, 415, 3817, 304, 1928, 1023, 3295, 298, 2948, 19810, 28723, 13, 2287, 415, 9378, 1212, 1023, 3295, 298, 396, 2992, 13, 260, 13, 2287, 415, 2245, 349, 28747, 13, 2287, 15223, 4682, 1130

In [150]:
# def get_key_phrase(phrase):
#     response = ollama.generate("mistral", prompt=f"Given the sentence {phrase}, extract the key phrase. Answer with just the key phrase. Don't give any explanations. For example  for the sentence 'in weekend shootings' answer with just 'weekend shootings'")
#     return (response["response"])
# get_key_phrase("the weekend shootings")

In [34]:
response['response']

' (Several hundred residents of a drug-torn neighborhood, protest, crack cocaine)\n(Residents, march, through the streets)\n(Protesters, shout, crack cocaine eradication)\n(Rev. Cecil Williams, lead, march and rally)\n(People, participate, in the march and rally)\n(Weeks-long planning, interrupted, drive-by ambush)\n(Shootings, leave, 2 people dead and 10 injured)\n(Community members, pray, complete eradication of crack cocaine)\n(Rev. Cecil Williams, say, shootings gave people another reason to participate)'

In [13]:
s.get_most_similar_word("Several hundred residents")

'residents'

In [28]:

import instructor
from pydantic import BaseModel, Field
from openai import OpenAI
from typing import List

# Define your desired output structure
class Character(BaseModel):
    name: str
    age: int
    fact: List[str] = Field(..., description="A list of facts about the character")

class Triplet(BaseModel):
    subject: str = Field(description='The subject of the triplet. It is an entity')
    relation: str = Field(description='The relation of the triplet. It is an action')
    object: str = Field(description='The object of the triplet. It it an entity')
    
client = instructor.from_openai(
    OpenAI(
        base_url="http://localhost:11434/v1",
        api_key="ollama",  # required, but unused
    ),
    mode=instructor.Mode.JSON,
)



In [33]:

# resp = client.chat.completions.create(
#     model="mistral",
#     messages=[
#         {
#             "role": "user",
#             "content": "Tell me about the Harry Potter",
#         }
#     ],
#     response_model=Character,
# )


template = f"""Task:Generate triplets from the following text.
    Instructions'
    The triplet should be in the format (<subject>, <relation>, <object>)

    The text is:
    Several hundred residents of a drug-torn neighborhood marched through the
    streets Sunday in an protest over crack cocaine spurred by weekend shootings
    that left 2 people dead and 10 injured.
    
    ''We are going to march and shout and sing and pray till this crack cocaine is
    completely eradicated from our community,'' said the Rev. Cecil Williams, who
    led the march through the Ocean View neighborhood.
    
    Although the march and rally had been planned for several weeks, a drive-by
    ambush and another shooting less than two miles away in the Bayview-Hunters
    Point district gave people another reason to participate, Mr. Williams said"""

     
# template = f"""Task:Decompose the triplet -> {triplet}
#     ##Instructions
#     ##If the triplet can be decomposed,return the new triplet. Else, return an empty string ""
#     ##The triplet should be in the format (<subject>, <relation type>, <object>)
#     ##The subject and object should refer to specific entities.
#     ##The relation type should refer to an action
#     ##Return only the triplets seperated by new lines. Do not explain the reason for returning the results
    
#     ##Example Given the triplet "People - participate - in the march and rally", return the 2 triplets
#     "People - participate - march"
#     "People - participate - rally"

#     ##Example Given the triplet "Several hundred residents of a drug-torn neighborhood -  protest -  crack cocaine", return the triplets
#     "residents - live in - drug-torn neighbourhood"
#     "residents - protest -  crack cocaine"

#     ##Example Given the triplet "residents -  march - streets", return an empty string "" as this triplet cannot be further decomposed
#     """

resp = client.chat.completions.create(
    model="mistral",
    messages=[
        {
            "role": "user",
            "content": template,
        }
    ],
    response_model=Triplet,
)


# resp = client.completions.create(
#     model="mistral",
#     prompt=template,
#     response_model=Triplet,
# )

print(resp.model_dump_json(indent=2))

APITimeoutError: Request timed out.

In [6]:
class KG:
    def __init__(self,):
        self.triplets = []

    def add_triplets(self, triplets : List):
        self.triplets.extend(triplets)


In [7]:
class TripletGenerator:

    def __init__(self, text : str, s : SemanticSimilarity, e : KeywordExtractor, doc_name : str):
        self.s = s
        self.e = e
        self.doc_name = doc_name
        self.text = text
        self.pattern = r"\((.*?)\)"
        self.model_name = "mistral"
        self.template = f"""Task:Generate triplets from the following text.
            Instructions'
            The triplet should be in the format (<subject>, <relation type>, <object>)
            The subject and object should refer to specific entities.
            The relation type should refer to an action
            
            The text is:
            {self.text}"""
        
        self.triplets = self._extract_triplets()

    def _get_entities_in_phrase(self, phrase) -> List:
        results = self.e.extract_named_entities(phrase)
        return results if results else [phrase]

        
    def _link_entities(self,subj,rel,obj):
        available_subj = self.s.get_most_similar_word(subj)
        if available_subj:
            subj = available_subj

        available_rel = self.s.get_most_similar_relation(rel)
        if available_rel:
            rel = available_rel
        else:
            self.s.add_relation(rel)
            
        available_obj = self.s.get_most_similar_word(obj)
        if available_obj:
            obj = available_obj

        return subj, rel, obj

    def refine(self, phrase):
        phrase = phrase.strip()
        phrase = phrase.lower()
        phrase = re.sub(r'[,\.!?]', '', phrase)
        phrase = re.sub(r'[^a-z0-9\s]', ' ', phrase)
        phrase = re.sub(r"^\s*(?:the|a)\s+", "", phrase, flags=re.IGNORECASE)
        phrase = re.sub(r'\s+', '_', phrase)
        return phrase
        
    def _refine_triplets(self, subj, rel, obj): #for example for a triplet Bill and John - played - Baseball, it will be split into two triplets with subjects being Bill and John 
        subj_nouns = self._get_entities_in_phrase(subj)
        obj_nouns = self._get_entities_in_phrase(obj)
        results = []
        for s in subj_nouns:
            for o in obj_nouns:
                s,rel,o = self.refine(s),self.refine(rel),self.refine(o)
                results.append((s,rel,o))
        return results

    def _add_doc_name_to_triplets(self, triplets):
        
        return [(w,x,y,z) for (w,x,y),z in zip(triplets,([self.doc_name] * len(triplets)))]

    def _add_doc_node(self, triplets):
        doc_triplets = []
        # doc_name = re.sub(r'[\/]', '_', self.doc_name)
        # doc_name = self.refine(doc_name)
        for t in triplets:
            # doc_triplets.append((t[0],"filepath",doc_name))
            doc_triplets.append((t[0],"filepath",self.doc_name))
        triplets.extend(doc_triplets)
        return triplets
        
    def _extract_triplets(self):
        triplet_results = []
        
        response = ollama.generate(model=self.model_name, prompt=self.template)
        
        for line in response['response'].split("\n"):
            matches = re.findall(self.pattern, line)
            if not matches:
                continue
            triplet = matches[0].split(",")
            if len(triplet) < 3:
                continue
            subj,rel,obj = triplet[0]," ".join(triplet[1:-1]), triplet[-1]
            subj,rel,obj = self._link_entities(subj, rel, obj)
            refined_triplets = self._refine_triplets(subj,rel,obj)
            # refined_triplets = self._add_doc_name_to_triplets(refined_triplets)
            refined_triplets = self._add_doc_node(refined_triplets)
            triplet_results.extend(refined_triplets)
            # triplet_results.append((subj.strip(),rel.strip(),obj.strip()))
        
        return triplet_results
    

        
    def get_triplets(self):
        return self.triplets
        
        
        
        

In [44]:
%%time
folder_path = "/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000"
# folder_path = "/home/niamatzawad/niamatzawad/Datasets/UTDBox/demoNY/splitted"

s = SemanticSimilarity()
kwe = KeywordExtractor()
kg = KG()

folder_objects = os.listdir(folder_path)
for i, filename in enumerate(folder_objects):
    if os.path.isfile(os.path.join(folder_path, filename)):
        with open(os.path.join(folder_path, filename), 'r') as file:
            text = file.read()
            text_splitted = [text[i * 1900:(i+1) *1900] for i in range(len(text)//1900)]
            start_text_time = time.time()
            for text_s in tqdm(text_splitted):
                start_subtext_time = time.time()
                try:
                    named_entities = kwe.extract_named_entities(text_s)
                except Exception as e:
                    continue
                s.generate_reference(named_entities)
                t = TripletGenerator(text_s, s, kwe, os.path.join(folder_path, filename))
                triplets = t.get_triplets()
                kg.add_triplets(triplets)
                print(triplets)
                print(f"Time to create triplets for current subtext - {time.time() - start_subtext_time}")
                
        print(f"Finished processing {i+1}/ {len(folder_objects)} files")
        print(f"Total time taken for current text - {time.time() - start_text_time}")
        print("---")
            
kg.triplets

  6%|██▍                                         | 1/18 [00:04<01:20,  4.76s/it]

Time to create triplets for current subtext - 4.760420799255371
[('rose_dale_parents', 'resist', 'schools_chancellor_frank_j_mac_chi_aro_la'), ('rose_dale_parents', 'filepath', '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8102099-8103008.TXT'), ('charles_cip_olla', 'lead', 'rose_dale_parents'), ('sandra_pet_ker', 'lead', 'rose_dale_parents'), ('charles_cip_olla', 'filepath', '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8102099-8103008.TXT'), ('sandra_pet_ker', 'filepath', '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8102099-8103008.TXT'), ('schools_chancellor_frank_j', 'announce', 'students'), ('schools_chancellor_frank_j', 'announce', 'rose_dale_annex'), ('schools_chancellor_frank_j', 'announce', 'main_building'), ('schools_chancellor_frank_j', 'announce', 'springfield_gardens'), ('schools_chancellor_frank_j', 'filepath', '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8102099-8103008.TXT'), ('sch

 11%|████▉                                       | 2/18 [00:07<01:01,  3.85s/it]

Time to create triplets for current subtext - 3.2096378803253174
[('annex', 'prevent', 'board_education'), ('annex', 'filepath', '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8102099-8103008.TXT'), ('parents', 'announce', 'boycott_classes_starting_tomorrow'), ('p_138_195', 'announce', 'boycott_classes_starting_tomorrow'), ('parents', 'filepath', '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8102099-8103008.TXT'), ('p_138_195', 'filepath', '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8102099-8103008.TXT'), ('organizers', 'call_on', 'parents_pupils'), ('organizers', 'call_on', 'p_138_195'), ('organizers', 'filepath', '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8102099-8103008.TXT'), ('organizers', 'filepath', '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8102099-8103008.TXT'), ('mayor_koch', 'urge', 'protesting_parents'), ('mayor_koch', 'urge', 'school_building'), ('mayor_koch

 17%|███████▎                                    | 3/18 [00:09<00:44,  2.99s/it]

...

 80%|████████████████████████████████████         | 4/5 [02:20<00:35, 35.11s/it]

Time to create triplets for current subtext - 34.74561357498169
[('metropolitan_edison_company', 'increased', 'consumers'), ('metropolitan_edison_company', 'filepath', '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8010038-8011002.TXT')]


100%|█████████████████████████████████████████████| 5/5 [02:59<00:00, 35.90s/it]

Time to create triplets for current subtext - 38.86166214942932
[('mission', 'criticized_by', 'metropolitan_edison_company'), ('mission', 'filepath', '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8010038-8011002.TXT'), ('metropolitan_edison_company', 'agree_on', 'human_error_and_instrument_failures'), ('metropolitan_edison_company', 'filepath', '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8010038-8011002.TXT'), ('westchester_county_legislator_richard_l_bro', 'said_that', 'public'), ('westchester_county_legislator_richard_l_bro', 'said_that', 'con_edison'), ('westchester_county_legislator_richard_l_bro', 'filepath', '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8010038-8011002.TXT'), ('westchester_county_legislator_richard_l_bro', 'filepath', '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8010038-8011002.TXT'), ('protesters', 'filed_claims_for', 'p_c'), ('protesters', 'filepath', '/home/niamatzawad/n

[('rose_dale_parents', 'resist', 'schools_chancellor_frank_j_mac_chi_aro_la'),
 ('rose_dale_parents',
  'filepath',
  '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8102099-8103008.TXT'),
 ('charles_cip_olla', 'lead', 'rose_dale_parents'),
 ('sandra_pet_ker', 'lead', 'rose_dale_parents'),
 ('charles_cip_olla',
  'filepath',
  '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8102099-8103008.TXT'),
 ('sandra_pet_ker',
  'filepath',
  '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8102099-8103008.TXT'),
 ('schools_chancellor_frank_j', 'announce', 'students'),
 ('schools_chancellor_frank_j', 'announce', 'rose_dale_annex'),
 ('schools_chancellor_frank_j', 'announce', 'main_building'),
 ('schools_chancellor_frank_j', 'announce', 'springfield_gardens'),
 ('schools_chancellor_frank_j',
  'filepath',
  '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8102099-8103008.TXT'),
 ('schools_chancellor_frank_j',
  'filepath

In [47]:
def retrieve_text_from_filepath(filepath):
    with open(filepath,'r') as f:
        t = f.read()
        return t


In [48]:
kg.triplets

[('rose_dale_parents', 'resist', 'schools_chancellor_frank_j_mac_chi_aro_la'),
 ('rose_dale_parents',
  'filepath',
  '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8102099-8103008.TXT'),
 ('charles_cip_olla', 'lead', 'rose_dale_parents'),
 ('sandra_pet_ker', 'lead', 'rose_dale_parents'),
 ('charles_cip_olla',
  'filepath',
  '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8102099-8103008.TXT'),
 ('sandra_pet_ker',
  'filepath',
  '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8102099-8103008.TXT'),
 ('schools_chancellor_frank_j', 'announce', 'students'),
 ('schools_chancellor_frank_j', 'announce', 'rose_dale_annex'),
 ('schools_chancellor_frank_j', 'announce', 'main_building'),
 ('schools_chancellor_frank_j', 'announce', 'springfield_gardens'),
 ('schools_chancellor_frank_j',
  'filepath',
  '/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000/NYT-8102099-8103008.TXT'),
 ('schools_chancellor_frank_j',
  'filepath

In [9]:
a = "`"+"hi"+"`"
a

'`hi`'

In [95]:
from py2neo import Graph, Node, Relationship



# Connect to the Neo4j database
graph = Graph("neo4j://localhost:7687", auth=("neo4j", "password"))
graph.delete_all()

triplets = kg.triplets

# Create the nodes and relationships
for subject, predicate, obj in triplets:
    # Create the subject node
    try:
        n = graph.run(f"MATCH (n:{subject}) RETURN n;").data()
    except Exception as e:
        print(f"Problem with subject - {subject}")
        continue

    if n:
        subject_node = n[0]["n"]
    else:
        subject_node = Node(subject, id=subject)
        graph.create(subject_node)

    if predicate == "filepath":
        # obj = re.sub("NYT Files", "'NYT Files'",obj)
        obj = "```"+obj+"```"
        print(obj)
        n = graph.run(f"MATCH (n:{obj}) RETURN n;").data()
        if n:
            print(f"{obj} found")
            print(n[0]["n"])
            object_node = n[0]["n"]
        else:
            # obj = re.sub("'NYT Files'", "NYT Files",obj)[1:-1]
            txt = retrieve_text_from_filepath(obj[3:-3])
            obj = obj[2:-2]
            object_node = Node(obj, text=txt)
            graph.create(object_node)
    else:
        try:
            n = graph.run(f"MATCH (n:{obj}) RETURN n;").data()
        except Exception as e:
            print(f"Problem with object - {obj}")
            continue
            
        if n:
            object_node = n[0]["n"]
        else:
            object_node = Node(obj, id=obj)
            graph.create(object_node)

    relationship = Relationship(subject_node, predicate, object_node)
    graph.merge(relationship)

print("Triplets added to the Neo4j database.")

('women_groups', 'issued_a_warning', 'president_carter', "A coalition of women's groups issued a warning to President Carter and the Democratic Party today that it does not consider the party's Presidential nomination settled despite the results of yesterday's primaries.")
('women_groups', 'filepath', '/home/niamatzawad/niamatzawad/Datasets/UTDBox/demoNY/unsplitted/NYT-8006015-8006027.TXT')
('iris_mitgang', 'noted', 'continuing_battle_for_the_nomination', "Iris Mitgang, chairman of the National Women's Political Caucus, noted that a continuing battle for the nomination would give leverage to women's rights activists seeking concessions from the candidates.")
('iris_mitgang', 'filepath', '/home/niamatzawad/niamatzawad/Datasets/UTDBox/demoNY/unsplitted/NYT-8006015-8006027.TXT')
('women_groups', 'demanded', 'democratic_party', "They cited several issues as 'bottom line' demands, including a commitment to ratify the proposed Federal equal rights amendment, abortion rights, and appointments

In [51]:
np.save('disambiguated_reference_list.npy', s.disambiguated_reference_list)    # .npy extension is added if not given
# disabiguated_reference_liit = np.load('disambiguated_reference_list.npy')

In [53]:
np.save('embedded_reference.npy', s.embedded_reference)    # .npy extension is added if not given
# embedded_reference = np.load('embedded_reference.npy')

In [ ]:
template = f"""Task:Generate triplets from the following text. For each triplet, mention the text from which the triplet was extracted
            ###Instructions:
            The triplet should be in the format (<subject>, <relation type>, <object>)
            The subject and object should refer to specific entities.
            The relation type should refer to an action.
            The text should be the paragraph from where the triplet was extracted. 
            
            The text is:
            Complaints against landlords in New York City are sharply on the rise, according
to public and private agencies concerned with the problem. The majority of the
complaints are about alleged overcharging, but apparently stricter landlord
enforcement of rental leases is also prompting inquiries from tenants.

Frank S. Kristof, president of a group that represents owners of rent-stabilized
apartments, said the association was getting 600 calls a day, compared with 20
or 30 a day not too long ago. He said that 62 percent of the calls were from
tenants and 38 percent from owners. He explained that he thought the upsurge was
''directly related to the tightness of the market.'' Landlords, he said, are
being ''sorely tempted by the eagerness of tenants to find homes.''
t
Jane Benedict, chairman and a founder of the 21-year-old Metropolitan Council of
Housing, the biggest citywide tenant union, said the council ''became aware
about a year ago of an accelerated effort by landlords to enforce technical
aspects of leases.''

''Our phones started jumping off their hooks,'' she said, ''and now we're
getting a flood of complaints,'' from increasingly organized tenants. By
invoking ''all kinds of technical matters,'' she said, the owners hope to ''get
rid of'' the existing occupant and bring in a new tenant at an increased rent.

Ellis Franke, executive director of the City Conciliation and Appeals Board,
which adjudicates tenant-landlord disputes in rentstabilized apartments, said
that complaints of overcharging in the six-month period ending in March were 47
percent greater than in the preceding half-year.

She added that complaints were ''now coming in at a rate that will be in the
neighborhood of 4,000 a year, and that's double what it was two years ago.''

Stephen Mindell, an assistant attorney general in the state Attorney General's
office, said it was ''very disturbing to us to find that in a substantial number
of cases, the self-regulating system of rent stabilization does not appear to be
working.'' Mr.  Mindell is in charge of a continuing investigation into rent
overcharges begun by the attorney general's office in February 1979.  His
office, he said, has obtained $700,000 in refunds to tenants.

New York City's rental housing essentially operates under two separate systems:
the Rent Stabilization Law for 850,000 apartments and the Rent Control Law for
400,000 others. Rent stabilization, which took effect in 1969, was fashioned to
be largely selfregulating. Rent control, which began under Federal auspices in
World War II and then was taken over by states and localities, is administered
here by the city government.

Rent increases in rent-stabilized apartments are set each year by the Rent
Guidelines Board. Under rent control, the city must approve any building's rent
increase. There is no public registration of leases for rent-stabilized
apartments to which a tenant can turn.  But for rent-controlled apartments, the
city keeps public records of rents."""


ollama.generate("mistral", prompt=template)

In [77]:
a = ('a','b')
b = ('z',)
new = a + b
new

('a', 'b', 'z')

In [141]:
class TripletGeneratorDemo:

    def __init__(self, text : str, s : SemanticSimilarity, e : KeywordExtractor, doc_name : str):
        self.s = s
        self.e = e
        self.doc_name = doc_name
        self.text = text
        self.pattern = r"\((.*?)\)"
        self.pattern_text = r"Text:\s(.*)"
        self.model_name = "mistral"
        self.template = f"""Task:Generate triplets from the following text. For each triplet, mention the text from which the triplet was extracted
            ###Instructions:
            The triplet should be in the format (<subject>, <relation type>, <object>)
            The subject and object should refer to specific entities.
            The relation type should refer to an action.
            The text should be the paragraph from where the triplet was extracted. Just extract the sentence verbatim and do not make modifications
            

             ###Example answer:
             (A, likes, B)
             Text: In the year 1993 A started liking B
             
            ###The text is:
            {self.text}"""
        
        self.triplets = self._extract_triplets()

    def _get_entities_in_phrase(self, phrase) -> List:
        results = self.e.extract_named_entities(phrase)
        return results if results else [phrase]

        
    def _link_entities(self,subj,rel,obj):
        available_subj = self.s.get_most_similar_word(subj)
        if available_subj:
            subj = available_subj

        available_rel = self.s.get_most_similar_relation(rel)
        if available_rel:
            rel = available_rel
        else:
            self.s.add_relation(rel)
            
        available_obj = self.s.get_most_similar_word(obj)
        if available_obj:
            obj = available_obj

        return subj, rel, obj

    def refine(self, phrase):
        phrase = phrase.strip()
        phrase = phrase.lower()
        phrase = re.sub(r'[,\.!?]', '', phrase)
        phrase = re.sub(r'[^a-z0-9\s]', ' ', phrase)
        phrase = re.sub(r"^\s*(?:the|a)\s+", "", phrase, flags=re.IGNORECASE)
        phrase = re.sub(r'\s+', '_', phrase)
        return phrase
        
    def _refine_triplets(self, subj, rel, obj): #for example for a triplet Bill and John - played - Baseball, it will be split into two triplets with subjects being Bill and John 
        subj_nouns = self._get_entities_in_phrase(subj)
        obj_nouns = self._get_entities_in_phrase(obj)
        results = []
        for s in subj_nouns:
            for o in obj_nouns:
                s,rel,o = self.refine(s),self.refine(rel),self.refine(o)
                results.append((s,rel,o))
        return results

    def _add_doc_name_to_triplets(self, triplets):
        
        return [(w,x,y,z) for (w,x,y),z in zip(triplets,([self.doc_name] * len(triplets)))]

    def _add_doc_node(self, triplets):
        doc_triplets = []
        # doc_name = re.sub(r'[\/]', '_', self.doc_name)
        # doc_name = self.refine(doc_name)
        for t in triplets:
            # doc_triplets.append((t[0],"filepath",doc_name))
            doc_triplets.append((t[0],"filepath",self.doc_name))
        triplets.extend(doc_triplets)
        return triplets


    def _extract_triplets(self):
        triplet_results = []
        
        response = ollama.generate(model=self.model_name, prompt=self.template)
        for line in response['response'].split("\n"):
            matches = re.findall(self.pattern, line)
            matches_text = re.findall(self.pattern_text, line)
            if not matches:
                if matches_text:
                    if len(triplet_results) > 1:
                        triplet_results[-2] = triplet_results[-2] + (matches_text[0],)  #Attach text to triplet
                continue
            triplet = matches[0].split(",")
            if len(triplet) < 3:
                continue
            subj,rel,obj = triplet[0]," ".join(triplet[1:-1]), triplet[-1]
            subj,rel,obj = self._link_entities(subj, rel, obj)
            refined_triplets = self._refine_triplets(subj,rel,obj)
            # refined_triplets = self._add_doc_name_to_triplets(refined_triplets)
            refined_triplets = self._add_doc_node(refined_triplets)
            triplet_results.extend(refined_triplets)
            # triplet_results.append((subj.strip(),rel.strip(),obj.strip()))
        
        return triplet_results
    

        
    def get_triplets(self):
        return self.triplets
        

In [142]:
%%time
# folder_path = "/home/niamatzawad/niamatzawad/Datasets/UTDBox/demoNY/unsplitted"
folder_path = "/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000"

s_demo = SemanticSimilarity()
kwe_demo = KeywordExtractor()
kg_demo = KG()

folder_objects = os.listdir(folder_path)
for i, filename in enumerate(folder_objects):
    if os.path.isfile(os.path.join(folder_path, filename)):
        with open(os.path.join(folder_path, filename), 'r') as file:
            text = file.read()
            text_splitted = [text[i * 1900:(i+1) *1900] for i in range(len(text)//1900)]
            start_text_time = time.time()
            for text_s in tqdm(text_splitted):
                start_subtext_time = time.time()
                try:
                    named_entities = kwe_demo.extract_named_entities(text_s)
                except Exception as e:
                    continue
                s_demo.generate_reference(named_entities)
                t = TripletGeneratorDemo(text_s, s_demo, kwe_demo, os.path.join(folder_path, filename))
                triplets = t.get_triplets()
                kg_demo.add_triplets(triplets)
                print(f"Time to create triplets for current subtext - {time.time() - start_subtext_time}")
                
        print(f"Finished processing {i+1}/ {len(folder_objects)} files")
        print(f"Total time taken for current text - {time.time() - start_text_time}")
        print("---")
            


  6%|██▍                                         | 1/18 [00:03<01:00,  3.56s/it]

Time to create triplets for current subtext - 3.561177968978882


 11%|████▉                                       | 2/18 [00:06<00:49,  3.12s/it]

Time to create triplets for current subtext - 2.8127353191375732


 17%|███████▎                                    | 3/18 [00:09<00:44,  2.96s/it]

...

Time to create triplets for current subtext - 11.587649822235107


 98%|██████████████████████████████████████████ | 45/46 [08:30<00:12, 12.23s/it]

Time to create triplets for current subtext - 12.983190298080444


 98%|██████████████████████████████████████████ | 45/46 [08:39<00:11, 11.55s/it]


KeyboardInterrupt: 

In [151]:
from py2neo import Graph, Node, Relationship



# Connect to the Neo4j database
graph = Graph("neo4j://localhost:7687", auth=("neo4j", "password"))
graph.delete_all()

triplets = kg_demo.triplets

# Create the nodes and relationships
for t in triplets:
    # Create the subject node
    subject, predicate, obj = t[0],t[1],t[2]
    context = None
    if len(t) == 4:
        context = t[3]
    
    try:
        n = graph.run(f"MATCH (n:{subject}) RETURN n;").data()
    except Exception as e:
        print(f"Problem with subject - {subject}")
        continue

    if n:
        subject_node = n[0]["n"]
    else:
        subject_node = Node(subject, id=subject)
        graph.create(subject_node)

    if predicate == "filepath":
        # obj = re.sub("NYT Files", "'NYT Files'",obj)
        obj = "```"+obj+"```"
        context = retrieve_text_from_filepath(obj[3:-3])
        n = graph.run(f"MATCH (n:{obj}) RETURN n;").data()
        if n:
            # print(n[0]["n"])
            object_node = n[0]["n"]
        else:
            # obj = re.sub("'NYT Files'", "NYT Files",obj)[1:-1]
            
            obj = obj[2:-2]
            object_node = Node(obj, id=obj)
            graph.create(object_node)
    else:
        try:
            n = graph.run(f"MATCH (n:{obj}) RETURN n;").data()
        except Exception as e:
            print(f"Problem with object - {obj}")
            continue
            
        if n:
            object_node = n[0]["n"]
        else:
            object_node = Node(obj, id=obj, text=context)
            graph.create(object_node)

    relationship = Relationship(subject_node, predicate, object_node, text=context)
    graph.merge(relationship)

print("Triplets added to the Neo4j database.")

Problem with object - 23_1
Problem with object - 000_years_old
Problem with object - 77_percent
Problem with subject - 15_year_old_boy
Problem with subject - 15_year_old_boy
Problem with subject - 17
Problem with subject - 17
Problem with object - 
Problem with object - 1965_march
Problem with object - 85_counts_in_an_indictment
Problem with object - 400_supporters
Problem with object - 000
Problem with object - 500_student_loan
Problem with object - 2_3_5
Problem with object - 200
Problem with object - 42_more
Problem with object - 100_million_gallons_of_low_level_radioactive_waste
Problem with object - 000_weekly
Problem with object - 000_in_the_initial_phase_of_the_private_survey
Problem with subject - 1_600_people
Problem with subject - 1_600_people
Problem with subject - 400_organizations
Problem with subject - 400_organizations
Problem with subject - 71_st_precinct
Problem with subject - 71_st_precinct
Problem with subject - 71_st_precinct
Problem with subject - 71_st_precinct
Pr

In [139]:
%%time
# folder_path = "/home/niamatzawad/niamatzawad/Datasets/UTDBox/demoNY/unsplitted"
folder_path = "/home/niamatzawad/niamatzawad/Datasets/UTDBox/NYT Files/1-1000"

s_demo = SemanticSimilarity()
kwe_demo = KeywordExtractor()
kg_demo = KG()

folder_objects = os.listdir(folder_path)
for i, filename in enumerate(folder_objects):
    if os.path.isfile(os.path.join(folder_path, filename)):
        with open(os.path.join(folder_path, filename), 'r') as file:
            text = file.read()
            text_splitted = [text[i * 1900:(i+1) *1900] for i in range(len(text)//1900)]
            start_text_time = time.time()
            for text_s in tqdm(text_splitted):
                start_subtext_time = time.time()
                try:
                    named_entities = kwe_demo.extract_named_entities(text_s)
                except Exception as e:
                    continue
                s_demo.generate_reference(named_entities)
                t = TripletGeneratorDemo(text_s, s_demo, kwe_demo, os.path.join(folder_path, filename))
                triplets = t.get_triplets()
                kg_demo.add_triplets(triplets)
                print(f"Time to create triplets for current subtext - {time.time() - start_subtext_time}")
                
        print(f"Finished processing {i+1}/ {len(folder_objects)} files")
        print(f"Total time taken for current text - {time.time() - start_text_time}")
        print("---")
            


  0%|                                                    | 0/18 [00:00<?, ?it/s]Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


{'model': 'mistral', 'created_at': '2024-04-25T23:27:58.712343774Z', 'response': ' (Parents of Rosedale, refuse, Send their children to the main building in Springfield Gardens)\nText: Parents of Rosedale vowed not to send their children to the school out of the neighborhood.\n\n(Charles Cipolla, leads, Protest against the closing of the Rosedale annex)\nText: Charles Cipolla, a former local school board member and a leader of the parents\' protest, stood atop a lunchroom table under one of the room’s two basketball hoops.\n\n(Sandra Petker, adds, Voice to the protest of sending children to the main building in Springfield Gardens)\nText: Another protest leader, Sandra Petker, added that "We will not allow our children to go."', 'done': True, 'context': [733, 16289, 28793, 28705, 10290, 28747, 23342, 22212, 1074, 477, 272, 2296, 2245, 28723, 1263, 1430, 2629, 7081, 28725, 4389, 272, 2245, 477, 690, 272, 2629, 7081, 403, 25081, 13, 17422, 774, 6060, 8373, 28747, 13, 17422, 415, 2629, 70

  6%|██▍                                         | 1/18 [00:05<01:26,  5.09s/it]

Time to create triplets for current subtext - 5.085960626602173


 11%|████▉                                       | 2/18 [00:08<01:03,  3.94s/it]

...

Time to create triplets for current subtext - 34.45197105407715
{'model': 'mistral', 'created_at': '2024-04-26T04:55:52.893329783Z', 'response': " Triplet 1:\n(Con Edison, decides, to charge customers)\nText: Con Edison has planned to begin charging its 2.7 million electric customers an additional 'fuel adjustment charge' reflecting the costs starting on Nov. 10.\n\nTriplet 2:\n(State Public Service Commission, has the right, to review increase)\nText: However, he added that the commission had the right to review the increase.\n\nTriplet 3:\n(Nuclear Regulatory Commission, begins, investigation)\nText: At his request, a House subcommittee had begun an investigation of events preceding the discovery of the water leak that led to the shutdown of the reactor on Oct. 20.", 'done': True, 'context': [733, 16289, 28793, 28705, 10290, 28747, 23342, 22212, 1074, 477, 272, 2296, 2245, 28723, 1263, 1430, 2629, 7081, 28725, 4389, 272, 2245, 477, 690, 272, 2629, 7081, 403, 25081, 13, 17422, 774, 60

 80%|████████████████████████████████████         | 4/5 [02:20<00:35, 35.21s/it]

Time to create triplets for current subtext - 35.78112840652466
{'model': 'mistral', 'created_at': '2024-04-26T04:56:29.748372098Z', 'response': ' Triplet 1: (Con Edison officials, have reported, testing, repairs and replacement of plumbing)\nText: Con Edison officials have reported that testing, repairs and replacement of plumbing in the nuclear reactor may keep the plant closed for several months.\n\nTriplet 2: (Critics of Con Edison, questioned, Con Edison, assessing its customers)\nText: Critics of Con Edison questioned whether Con Edison was acting properly in assessing its customers for the added costs.\n\nTriplets 3: (Con Edison spokesman, said, customers, losing savings)\nText: A Con Edison spokesman said that its customers were "losing savings" they had been enjoying from the use of cheaper nuclear power.\n\nTriplet 4: (Utility\'s spokesman, called, increase, best guess)\nText: One Con Edison spokesman called the increase a "best guess" of the added cost of oil to produce elec

100%|█████████████████████████████████████████████| 5/5 [02:57<00:00, 35.49s/it]

Time to create triplets for current subtext - 36.99641036987305
Finished processing 71/ 71 files
Total time taken for current text - 177.4482867717743
---
CPU times: user 5h 48min 34s, sys: 20min 44s, total: 6h 9min 19s
Wall time: 5h 28min 38s


In [149]:
np.save('disambiguated_reference_list_kg_demo.npy', s_demo.disambiguated_reference_list)    # .npy extension is added if not given
np.save('embedded_reference_kg_demo.npy', s_demo.embedded_reference)    # .npy extension is added if not given


In [1]:
s_demo.get_most_similar_entities("dua lipa")

NameError: name 's_demo' is not defined